# MA Cross Strategy

In [1]:
import datetime
import numpy as np
import talib
import matplotlib.pyplot as plt
import mplfinance as mpf
from math import comb
from dataset import kline_data
from strategies import ma_cross_signal
from dateutil import parser

In [2]:
mas = [talib.SMA, talib.EMA, talib.DEMA, talib.TEMA, talib.TRIMA, talib.WMA, talib.KAMA]
ma_periods = np.arange(5, 201, 5)
position_sizes = 0.01 * np.arange(1, 101)

In [26]:
btc_1d = kline_data(interval='1d')

Last saved data candle close time: 2021-08-14


In [27]:
np.array(btc_1d['open_time'])[-1]

'2021-08-13'

## 4H Timeframe

In [3]:
btc_4h = kline_data(interval='4h')
btc_4h = btc_4h.set_index(btc_4h['open_time'].map(parser.parse))
close = np.array(btc_4h['close'])
high = np.array(btc_4h['high'])
low = np.array(btc_4h['low'])

n_candles = len(close)
n_train = int(0.75 * n_candles)
n_test = n_candles - n_train
train = close[:n_train]
test = close[n_train:]

Last saved data candle close time: 2021-08-14 16:00:00


In [4]:
fee = 0.001
sl = 0.1
# Training
ct = 1
results = {}
n_runs = len(mas) * len(mas) * comb(len(ma_periods), 2)
print(f'Total runs: {n_runs}')
start = datetime.datetime.now()
for fast_ma in mas:
    for slow_ma in mas:
        for fast_period in ma_periods[:-1]:
            for slow_period in ma_periods[np.where(ma_periods == fast_period)[0][0] + 1:]:
                cash = 1000
                p = 1  # position size
                print(f'*** {ct} / {n_runs}')
                buys, sells = ma_cross_signal(fast_ma(train, timeperiod=fast_period),
                                              slow_ma(train, timeperiod=slow_period))
                buys = buys * train
                sells = sells * train
                orders = np.nan_to_num(buys) - np.nan_to_num(sells)
                orders = orders[orders != 0]
                if orders[0] < 0:
                    orders = np.delete(orders, 0)
                if orders[-1] > 0:
                    orders = np.delete(orders, -1)
                buys = orders[0::2]
                sells = - orders[1::2]
                profits = (sells / buys - 1) * (1 - fee)
                for profit in profits:
                    cash += profit * p * cash
                results[cash] = (fast_ma, slow_ma, fast_period, slow_period)
                ct += 1
                elapsed = datetime.datetime.now() - start
                print(f'Elapsed time: {elapsed}')
                print(f'ETA: {(elapsed.seconds * n_runs / ct - elapsed.seconds) / 60} minutes')
max_cash = max(list(results.keys()))
print(f'Max cash: {max_cash}')
best_settings = results[max_cash]
print(f'Best settins: {best_settings}')

Total runs: 38220
*** 1 / 38220
Elapsed time: 0:00:00.045379
ETA: 0.0 minutes
*** 2 / 38220
Elapsed time: 0:00:00.088951
ETA: 0.0 minutes
*** 3 / 38220
Elapsed time: 0:00:00.135953
ETA: 0.0 minutes
*** 4 / 38220
Elapsed time: 0:00:00.176447
ETA: 0.0 minutes
*** 5 / 38220
Elapsed time: 0:00:00.201121
ETA: 0.0 minutes
*** 6 / 38220
Elapsed time: 0:00:00.230043
ETA: 0.0 minutes
*** 7 / 38220
Elapsed time: 0:00:00.255750
ETA: 0.0 minutes
*** 8 / 38220
Elapsed time: 0:00:00.298666
ETA: 0.0 minutes
*** 9 / 38220
Elapsed time: 0:00:00.344664
ETA: 0.0 minutes
*** 10 / 38220
Elapsed time: 0:00:00.381663
ETA: 0.0 minutes
*** 11 / 38220
Elapsed time: 0:00:00.413738
ETA: 0.0 minutes
*** 12 / 38220
Elapsed time: 0:00:00.459974
ETA: 0.0 minutes
*** 13 / 38220
Elapsed time: 0:00:00.500797
ETA: 0.0 minutes
*** 14 / 38220
Elapsed time: 0:00:00.524810
ETA: 0.0 minutes
*** 15 / 38220
Elapsed time: 0:00:00.548797
ETA: 0.0 minutes
*** 16 / 38220
Elapsed time: 0:00:00.572176
ETA: 0.0 minutes
*** 17 / 38220


Elapsed time: 0:00:04.100916
ETA: 20.99118457300275 minutes
*** 121 / 38220
Elapsed time: 0:00:04.127266
ETA: 20.818579234972677 minutes
*** 122 / 38220
Elapsed time: 0:00:04.151621
ETA: 20.648780487804878 minutes
*** 123 / 38220
Elapsed time: 0:00:04.185190
ETA: 20.48172043010753 minutes
*** 124 / 38220
Elapsed time: 0:00:04.220502
ETA: 20.317333333333334 minutes
*** 125 / 38220
Elapsed time: 0:00:04.254173
ETA: 20.155555555555555 minutes
*** 126 / 38220
Elapsed time: 0:00:04.292423
ETA: 19.996325459317585 minutes
*** 127 / 38220
Elapsed time: 0:00:04.329348
ETA: 19.839583333333334 minutes
*** 128 / 38220
Elapsed time: 0:00:04.366424
ETA: 19.685271317829457 minutes
*** 129 / 38220
Elapsed time: 0:00:04.400348
ETA: 19.533333333333335 minutes
*** 130 / 38220
Elapsed time: 0:00:04.422348
ETA: 19.383715012722647 minutes
*** 131 / 38220
Elapsed time: 0:00:04.447448
ETA: 19.236363636363638 minutes
*** 132 / 38220
Elapsed time: 0:00:04.484505
ETA: 19.091228070175436 minutes
*** 133 / 38220
E

Elapsed time: 0:00:07.741176
ETA: 18.938888888888886 minutes
*** 234 / 38220
Elapsed time: 0:00:07.785143
ETA: 18.857801418439713 minutes
*** 235 / 38220
Elapsed time: 0:00:07.816091
ETA: 18.777401129943502 minutes
*** 236 / 38220
Elapsed time: 0:00:07.863629
ETA: 18.697679324894516 minutes
*** 237 / 38220
Elapsed time: 0:00:07.910563
ETA: 18.61862745098039 minutes
*** 238 / 38220
Elapsed time: 0:00:07.926185
ETA: 18.54023709902371 minutes
*** 239 / 38220
Elapsed time: 0:00:07.957865
ETA: 18.4625 minutes
*** 240 / 38220
Elapsed time: 0:00:08.010982
ETA: 21.0118948824343 minutes
*** 241 / 38220
Elapsed time: 0:00:08.032138
ETA: 20.924517906336085 minutes
*** 242 / 38220
Elapsed time: 0:00:08.047916
ETA: 20.837860082304527 minutes
*** 243 / 38220
Elapsed time: 0:00:08.079149
ETA: 20.75191256830601 minutes
*** 244 / 38220
Elapsed time: 0:00:08.094778
ETA: 20.666666666666668 minutes
*** 245 / 38220
Elapsed time: 0:00:08.126018
ETA: 20.58211382113821 minutes
*** 246 / 38220
Elapsed time: 0:

Elapsed time: 0:00:11.400645
ETA: 20.0097502401537 minutes
*** 347 / 38220
Elapsed time: 0:00:11.443673
ETA: 19.951724137931034 minutes
*** 348 / 38220
Elapsed time: 0:00:11.484333
ETA: 19.894030563514807 minutes
*** 349 / 38220
Elapsed time: 0:00:11.536984
ETA: 19.836666666666666 minutes
*** 350 / 38220
Elapsed time: 0:00:11.583541
ETA: 19.779629629629632 minutes
*** 351 / 38220
Elapsed time: 0:00:11.609542
ETA: 19.722916666666666 minutes
*** 352 / 38220
Elapsed time: 0:00:11.643001
ETA: 19.666525023607175 minutes
*** 353 / 38220
Elapsed time: 0:00:11.679429
ETA: 19.61045197740113 minutes
*** 354 / 38220
Elapsed time: 0:00:11.703430
ETA: 19.554694835680753 minutes
*** 355 / 38220
Elapsed time: 0:00:11.726891
ETA: 19.499250936329588 minutes
*** 356 / 38220
Elapsed time: 0:00:11.749961
ETA: 19.444117647058825 minutes
*** 357 / 38220
Elapsed time: 0:00:11.772958
ETA: 19.389292364990688 minutes
*** 358 / 38220
Elapsed time: 0:00:11.796266
ETA: 19.33477251624884 minutes
*** 359 / 38220
Ela

Elapsed time: 0:00:14.890416
ETA: 19.323684210526316 minutes
*** 456 / 38220
Elapsed time: 0:00:14.916418
ETA: 19.280889861415023 minutes
*** 457 / 38220
Elapsed time: 0:00:14.941605
ETA: 19.238282387190683 minutes
*** 458 / 38220
Elapsed time: 0:00:14.970648
ETA: 19.1958605664488 minutes
*** 459 / 38220
Elapsed time: 0:00:14.997173
ETA: 19.153623188405795 minutes
*** 460 / 38220
Elapsed time: 0:00:15.035807
ETA: 20.476681127982648 minutes
*** 461 / 38220
Elapsed time: 0:00:15.068249
ETA: 20.431818181818183 minutes
*** 462 / 38220
Elapsed time: 0:00:15.103887
ETA: 20.387149028077754 minutes
*** 463 / 38220
Elapsed time: 0:00:15.144634
ETA: 20.342672413793103 minutes
*** 464 / 38220
Elapsed time: 0:00:15.183099
ETA: 20.298387096774196 minutes
*** 465 / 38220
Elapsed time: 0:00:15.211514
ETA: 20.254291845493565 minutes
*** 466 / 38220
Elapsed time: 0:00:15.243924
ETA: 20.21038543897216 minutes
*** 467 / 38220
Elapsed time: 0:00:15.279131
ETA: 20.166666666666668 minutes
*** 468 / 38220
El

...

Elapsed time: 0:20:09.054362
ETA: 0.23251640906203572 minutes
*** 37784 / 38220
Elapsed time: 0:20:09.076487
ETA: 0.2319769749900767 minutes
*** 37785 / 38220
Elapsed time: 0:20:09.107835
ETA: 0.23143756947017285 minutes
*** 37786 / 38220
Elapsed time: 0:20:09.123459
ETA: 0.2308981925000656 minutes
*** 37787 / 38220
Elapsed time: 0:20:09.154706
ETA: 0.23035884407748503 minutes
*** 37788 / 38220
Elapsed time: 0:20:09.186351
ETA: 0.22981952420016494 minutes
*** 37789 / 38220
Elapsed time: 0:20:09.201973
ETA: 0.22928023286583918 minutes
*** 37790 / 38220
Elapsed time: 0:20:09.236142
ETA: 0.22874097007223781 minutes
*** 37791 / 38220
Elapsed time: 0:20:09.251843
ETA: 0.22820173581710226 minutes
*** 37792 / 38220
Elapsed time: 0:20:09.283092
ETA: 0.22766253009816637 minutes
*** 37793 / 38220
Elapsed time: 0:20:09.333794
ETA: 0.2271233529131602 minutes
*** 37794 / 38220
Elapsed time: 0:20:09.349504
ETA: 0.22658420425982134 minutes
*** 37795 / 38220
Elapsed time: 0:20:09.380766
ETA: 0.2260450

Elapsed time: 0:20:12.228280
ETA: 0.1748548506281016 minutes
*** 37892 / 38220
Elapsed time: 0:20:12.275229
ETA: 0.1743171562029943 minutes
*** 37893 / 38220
Elapsed time: 0:20:12.317078
ETA: 0.17377949015675162 minutes
*** 37894 / 38220
Elapsed time: 0:20:12.348356
ETA: 0.17324185248713395 minutes
*** 37895 / 38220
Elapsed time: 0:20:12.395826
ETA: 0.17270424319189412 minutes
*** 37896 / 38220
Elapsed time: 0:20:12.427065
ETA: 0.17216666226878108 minutes
*** 37897 / 38220
Elapsed time: 0:20:12.458411
ETA: 0.17162910971555145 minutes
*** 37898 / 38220
Elapsed time: 0:20:12.505417
ETA: 0.1710915855299618 minutes
*** 37899 / 38220
Elapsed time: 0:20:12.543141
ETA: 0.17055408970976108 minutes
*** 37900 / 38220
Elapsed time: 0:20:12.574386
ETA: 0.17001662225270972 minutes
*** 37901 / 38220
Elapsed time: 0:20:12.605632
ETA: 0.1694791831565605 minutes
*** 37902 / 38220
Elapsed time: 0:20:12.621256
ETA: 0.16894177241906996 minutes
*** 37903 / 38220
Elapsed time: 0:20:12.652503
ETA: 0.16840439

Elapsed time: 0:20:15.410148
ETA: 0.1199170943545217 minutes
*** 37995 / 38220
Elapsed time: 0:20:15.441397
ETA: 0.11938098747236457 minutes
*** 37996 / 38220
Elapsed time: 0:20:15.477576
ETA: 0.11884490880859175 minutes
*** 37997 / 38220
Elapsed time: 0:20:15.508827
ETA: 0.11830885836096741 minutes
*** 37998 / 38220
Elapsed time: 0:20:15.524451
ETA: 0.11777283612726705 minutes
*** 37999 / 38220
Elapsed time: 0:20:15.555701
ETA: 0.11723684210526245 minutes
*** 38000 / 38220
Elapsed time: 0:20:15.571321
ETA: 0.11670087629272909 minutes
*** 38001 / 38220
Elapsed time: 0:20:15.586945
ETA: 0.11616493868743874 minutes
*** 38002 / 38220
Elapsed time: 0:20:15.633813
ETA: 0.11562902928716312 minutes
*** 38003 / 38220
Elapsed time: 0:20:15.657905
ETA: 0.11509314808967398 minutes
*** 38004 / 38220
Elapsed time: 0:20:15.708153
ETA: 0.11455729509275064 minutes
*** 38005 / 38220
Elapsed time: 0:20:15.739391
ETA: 0.11402147029416483 minutes
*** 38006 / 38220
Elapsed time: 0:20:15.770950
ETA: 0.11348

Elapsed time: 0:20:18.377399
ETA: 0.06447150843854009 minutes
*** 38099 / 38220
Elapsed time: 0:20:18.408723
ETA: 0.06393700787401713 minutes
*** 38100 / 38220
Elapsed time: 0:20:18.446514
ETA: 0.06340253536652654 minutes
*** 38101 / 38220
Elapsed time: 0:20:18.477771
ETA: 0.06286809091386279 minutes
*** 38102 / 38220
Elapsed time: 0:20:18.526534
ETA: 0.06233367451381658 minutes
*** 38103 / 38220
Elapsed time: 0:20:18.542350
ETA: 0.06179928616418238 minutes
*** 38104 / 38220
Elapsed time: 0:20:18.573726
ETA: 0.06126492586274708 minutes
*** 38105 / 38220
Elapsed time: 0:20:18.621925
ETA: 0.06073059360730516 minutes
*** 38106 / 38220
Elapsed time: 0:20:18.669297
ETA: 0.0601962893956473 minutes
*** 38107 / 38220
Elapsed time: 0:20:18.685006
ETA: 0.05966201322556799 minutes
*** 38108 / 38220
Elapsed time: 0:20:18.716257
ETA: 0.059127765094857905 minutes
*** 38109 / 38220
Elapsed time: 0:20:18.731875
ETA: 0.05859354500131152 minutes
*** 38110 / 38220
Elapsed time: 0:20:18.763135
ETA: 0.0580

Elapsed time: 0:20:21.671199
ETA: 0.0063913316582898 minutes
*** 38208 / 38220
Elapsed time: 0:20:21.706814
ETA: 0.005858567353239626 minutes
*** 38209 / 38220
Elapsed time: 0:20:21.723155
ETA: 0.0053258309343088206 minutes
*** 38210 / 38220
Elapsed time: 0:20:21.770371
ETA: 0.004793122399310808 minutes
*** 38211 / 38220
Elapsed time: 0:20:21.802595
ETA: 0.004260441746047642 minutes
*** 38212 / 38220
Elapsed time: 0:20:21.833835
ETA: 0.003727788972340325 minutes
*** 38213 / 38220
Elapsed time: 0:20:21.849457
ETA: 0.0031951640759947018 minutes
*** 38214 / 38220
Elapsed time: 0:20:21.892313
ETA: 0.0026625670548204045 minutes
*** 38215 / 38220
Elapsed time: 0:20:21.907946
ETA: 0.002129997906634647 minutes
*** 38216 / 38220
Elapsed time: 0:20:21.954045
ETA: 0.0015974566292470626 minutes
*** 38217 / 38220
Elapsed time: 0:20:21.985957
ETA: 0.0010649432204710744 minutes
*** 38218 / 38220
Elapsed time: 0:20:22.017387
ETA: 0.000532893761392946 minutes
*** 38219 / 38220
Elapsed time: 0:20:22.033

In [5]:
ct = 1
results = {}
fast_ma, slow_ma, fast_period, slow_period = best_settings
for p in position_sizes:
    cash = 1000
    print(f'*** {ct} / {len(position_sizes)}')
    buys, sells = ma_cross_signal(fast_ma(train, timeperiod=fast_period),
                                  slow_ma(train, timeperiod=slow_period))
    buys = buys * train
    sells = sells * train
    orders = np.nan_to_num(buys) - np.nan_to_num(sells)
    orders = orders[orders != 0]
    if orders[0] < 0:
        orders = np.delete(orders, 0)
    if orders[-1] > 0:
        orders = np.delete(orders, -1)                        
    buys = orders[0::2]
    sells = - orders[1::2]
    profits = (sells / buys - 1) * (1 - fee)
    for profit in profits:
        cash += profit * p * cash
    results[cash] = p
    ct += 1
    elapsed = datetime.datetime.now() - start
    print(f'Elapsed time: {elapsed}')
    print(f'ETA: {(elapsed.seconds * n_runs / ct - elapsed.seconds) / 60} minutes')
max_cash = max(list(results.keys()))
print(f'Max cash: {max_cash}')
best_p = results[max_cash]
print(f'Best p: {best_p}')

*** 1 / 100
Elapsed time: 0:20:22.132109
ETA: 389186.63333333336 minutes
*** 2 / 100
Elapsed time: 0:20:22.166399
ETA: 259450.96666666667 minutes
*** 3 / 100
Elapsed time: 0:20:22.197154
ETA: 194583.13333333333 minutes
*** 4 / 100
Elapsed time: 0:20:22.238578
ETA: 155662.43333333332 minutes
*** 5 / 100
Elapsed time: 0:20:22.269822
ETA: 129715.3 minutes
*** 6 / 100
Elapsed time: 0:20:22.301826
ETA: 111181.63333333333 minutes
*** 7 / 100
Elapsed time: 0:20:22.318038
ETA: 97281.38333333333 minutes
*** 8 / 100
Elapsed time: 0:20:22.338834
ETA: 86470.07777777778 minutes
*** 9 / 100
Elapsed time: 0:20:22.373067
ETA: 77821.03333333334 minutes
*** 10 / 100
Elapsed time: 0:20:22.388945
ETA: 70744.54242424243 minutes
*** 11 / 100
Elapsed time: 0:20:22.420312
ETA: 64847.46666666667 minutes
*** 12 / 100
Elapsed time: 0:20:22.451639
ETA: 59857.63333333333 minutes
*** 13 / 100
Elapsed time: 0:20:22.483448
ETA: 55580.63333333333 minutes
*** 14 / 100
Elapsed time: 0:20:22.514713
ETA: 51873.9 minutes
*

In [6]:
# Testing
cash = 1000
p = best_p
buys, sells = ma_cross_signal(fast_ma(close, timeperiod=fast_period)[-n_test:],
                              slow_ma(close, timeperiod=slow_period)[-n_test:])
buys = buys * test
sells = sells * test
orders = np.nan_to_num(buys) - np.nan_to_num(sells)
orders = orders[orders != 0]
if orders[0] < 0:
    orders = np.delete(orders, 0)
if orders[-1] > 0:
    orders = np.delete(orders, -1)                        
buys = orders[0::2]
sells = - orders[1::2]
profits = (sells / buys - 1) * (1 - fee)
for profit in profits:
    cash += profit * p * cash
print(f'Test results - Final cash: {cash}')
print(f'Number of test days: {n_test / 6}')

Test results - Final cash: 2509.9190806542238
Number of test days: 364.0


## 1H Timeframe

In [3]:
btc_1h = kline_data(interval='1h')
btc_1h = btc_1h.set_index(btc_1h['open_time'].map(parser.parse))
close = np.array(btc_1h['close'])
high = np.array(btc_1h['high'])
low = np.array(btc_1h['low'])

n_candles = len(close)
n_train = int(0.75 * n_candles)
n_test = n_candles - n_train
train = close[:n_train]
test = close[n_train:]

Last saved data candle close time: 2021-08-11 15:00:00


In [4]:
fee = 0.001
# Training
ct = 1
results = {}
n_runs = len(mas) * len(mas) * comb(len(ma_periods), 2)
print(f'Total runs: {n_runs}')
start = datetime.datetime.now()
for fast_ma in mas:
    for slow_ma in mas:
        for fast_period in ma_periods[:-1]:
            for slow_period in ma_periods[np.where(ma_periods == fast_period)[0][0] + 1:]:
                cash = 1000
                p = 1  # position size
                print(f'*** {ct} / {n_runs}')
                buys, sells = ma_cross_signal(fast_ma(train, timeperiod=fast_period),
                                              slow_ma(train, timeperiod=slow_period))
                buys = buys * train
                sells = sells * train
                orders = np.nan_to_num(buys) - np.nan_to_num(sells)
                orders = orders[orders != 0]
                if orders[0] < 0:
                    orders = np.delete(orders, 0)
                if orders[-1] > 0:
                    orders = np.delete(orders, -1)                        
                buys = orders[0::2]
                sells = - orders[1::2]
                profits = (sells / buys - 1) * (1 - fee)
                for profit in profits:
                    cash += profit * p * cash
                results[cash] = (fast_ma, slow_ma, fast_period, slow_period)
                ct += 1
                elapsed = datetime.datetime.now() - start
                print(f'Elapsed time: {elapsed}')
                print(f'ETA: {(elapsed.seconds * n_runs / ct - elapsed.seconds) / 60} minutes')
max_cash = max(list(results.keys()))
print(f'Max cash: {max_cash}')
best_settings = results[max_cash]
print(f'Best settins: {best_settings}')

Total runs: 38220
*** 1 / 38220
Elapsed time: 0:00:00.143859
ETA: 0.0 minutes
*** 2 / 38220
Elapsed time: 0:00:00.279651
ETA: 0.0 minutes
*** 3 / 38220
Elapsed time: 0:00:00.401314
ETA: 0.0 minutes
*** 4 / 38220
Elapsed time: 0:00:00.577809
ETA: 0.0 minutes
*** 5 / 38220
Elapsed time: 0:00:00.699602
ETA: 0.0 minutes
*** 6 / 38220
Elapsed time: 0:00:00.805226
ETA: 0.0 minutes
*** 7 / 38220
Elapsed time: 0:00:00.929585
ETA: 0.0 minutes
*** 8 / 38220
Elapsed time: 0:00:01.033473
ETA: 70.76111111111112 minutes
*** 9 / 38220
Elapsed time: 0:00:01.167924
ETA: 63.68333333333333 minutes
*** 10 / 38220
Elapsed time: 0:00:01.315583
ETA: 57.89242424242424 minutes
*** 11 / 38220
Elapsed time: 0:00:01.431197
ETA: 53.06666666666667 minutes
*** 12 / 38220
Elapsed time: 0:00:01.573493
ETA: 48.983333333333334 minutes
*** 13 / 38220
Elapsed time: 0:00:01.714842
ETA: 45.483333333333334 minutes
*** 14 / 38220
Elapsed time: 0:00:01.875922
ETA: 42.45 minutes
*** 15 / 38220
Elapsed time: 0:00:02.005585
ETA: 

Elapsed time: 0:00:15.819243
ETA: 82.83695652173914 minutes
*** 115 / 38220
Elapsed time: 0:00:15.945211
ETA: 82.12068965517241 minutes
*** 116 / 38220
Elapsed time: 0:00:16.112928
ETA: 86.84444444444445 minutes
*** 117 / 38220
Elapsed time: 0:00:16.260841
ETA: 86.10621468926553 minutes
*** 118 / 38220
Elapsed time: 0:00:16.397278
ETA: 85.38039215686275 minutes
*** 119 / 38220
Elapsed time: 0:00:16.509094
ETA: 84.66666666666667 minutes
*** 120 / 38220
Elapsed time: 0:00:16.667872
ETA: 83.964738292011 minutes
*** 121 / 38220
Elapsed time: 0:00:16.830671
ETA: 83.27431693989071 minutes
*** 122 / 38220
Elapsed time: 0:00:16.959786
ETA: 82.59512195121951 minutes
*** 123 / 38220
Elapsed time: 0:00:17.091974
ETA: 87.04731182795699 minutes
*** 124 / 38220
Elapsed time: 0:00:17.218070
ETA: 86.34866666666667 minutes
*** 125 / 38220
Elapsed time: 0:00:17.325032
ETA: 85.66111111111111 minutes
*** 126 / 38220
Elapsed time: 0:00:17.447642
ETA: 84.98438320209974 minutes
*** 127 / 38220
Elapsed time: 

Elapsed time: 0:00:30.580268
ETA: 84.43333333333334 minutes
*** 225 / 38220
Elapsed time: 0:00:30.695656
ETA: 84.0575221238938 minutes
*** 226 / 38220
Elapsed time: 0:00:30.789034
ETA: 83.68502202643171 minutes
*** 227 / 38220
Elapsed time: 0:00:30.960782
ETA: 83.3157894736842 minutes
*** 228 / 38220
Elapsed time: 0:00:31.098416
ETA: 85.71477438136826 minutes
*** 229 / 38220
Elapsed time: 0:00:31.247816
ETA: 85.33985507246376 minutes
*** 230 / 38220
Elapsed time: 0:00:31.359953
ETA: 84.96818181818182 minutes
*** 231 / 38220
Elapsed time: 0:00:31.476743
ETA: 84.59971264367816 minutes
*** 232 / 38220
Elapsed time: 0:00:31.601016
ETA: 84.23440629470673 minutes
*** 233 / 38220
Elapsed time: 0:00:31.696226
ETA: 83.87222222222222 minutes
*** 234 / 38220
Elapsed time: 0:00:31.793901
ETA: 83.51312056737588 minutes
*** 235 / 38220
Elapsed time: 0:00:31.960800
ETA: 83.15706214689266 minutes
*** 236 / 38220
Elapsed time: 0:00:32.110927
ETA: 85.47510548523206 minutes
*** 237 / 38220
Elapsed time: 

Elapsed time: 0:00:45.342330
ETA: 84.81716417910448 minutes
*** 335 / 38220
Elapsed time: 0:00:45.521292
ETA: 84.5625 minutes
*** 336 / 38220
Elapsed time: 0:00:45.692396
ETA: 84.3093471810089 minutes
*** 337 / 38220
Elapsed time: 0:00:45.839892
ETA: 84.0576923076923 minutes
*** 338 / 38220
Elapsed time: 0:00:46.019276
ETA: 85.66991150442477 minutes
*** 339 / 38220
Elapsed time: 0:00:46.195154
ETA: 85.41568627450981 minutes
*** 340 / 38220
Elapsed time: 0:00:46.427949
ETA: 85.16295210166179 minutes
*** 341 / 38220
Elapsed time: 0:00:46.639124
ETA: 84.91169590643274 minutes
*** 342 / 38220
Elapsed time: 0:00:46.820396
ETA: 84.66190476190475 minutes
*** 343 / 38220
Elapsed time: 0:00:47.006651
ETA: 86.24864341085272 minutes
*** 344 / 38220
Elapsed time: 0:00:47.227485
ETA: 85.9963768115942 minutes
*** 345 / 38220
Elapsed time: 0:00:47.456809
ETA: 85.74556840077071 minutes
*** 346 / 38220
Elapsed time: 0:00:47.676557
ETA: 85.4962055715658 minutes
*** 347 / 38220
Elapsed time: 0:00:47.8592

Elapsed time: 0:01:06.789027
ETA: 93.37640449438203 minutes
*** 445 / 38220
Elapsed time: 0:01:06.994155
ETA: 93.16457399103139 minutes
*** 446 / 38220
Elapsed time: 0:01:07.236282
ETA: 94.36208053691276 minutes
*** 447 / 38220
Elapsed time: 0:01:07.431578
ETA: 94.14895833333334 minutes
*** 448 / 38220
Elapsed time: 0:01:07.639902
ETA: 93.93678544914626 minutes
*** 449 / 38220
Elapsed time: 0:01:07.844282
ETA: 93.72555555555556 minutes
*** 450 / 38220
Elapsed time: 0:01:08.077589
ETA: 94.91101256467111 minutes
*** 451 / 38220
Elapsed time: 0:01:08.319570
ETA: 94.69852507374632 minutes
*** 452 / 38220
Elapsed time: 0:01:08.544601
ETA: 94.4869757174393 minutes
*** 453 / 38220
Elapsed time: 0:01:08.731549
ETA: 94.27635829662262 minutes
*** 454 / 38220
Elapsed time: 0:01:08.940572
ETA: 94.06666666666666 minutes
*** 455 / 38220
Elapsed time: 0:01:09.144610
ETA: 95.23815789473684 minutes
*** 456 / 38220
Elapsed time: 0:01:09.353241
ETA: 95.02724288840263 minutes
*** 457 / 38220
Elapsed time:

...

Elapsed time: 1:29:52.226257
ETA: 1.08032268883829 minutes
*** 37766 / 38220
Elapsed time: 1:29:52.492012
ETA: 1.0779145815129596 minutes
*** 37767 / 38220
Elapsed time: 1:29:52.790732
ETA: 1.0755066017086847 minutes
*** 37768 / 38220
Elapsed time: 1:29:53.011906
ETA: 1.0732977662456809 minutes
*** 37769 / 38220
Elapsed time: 1:29:53.240297
ETA: 1.070889594916601 minutes
*** 37770 / 38220
Elapsed time: 1:29:53.500035
ETA: 1.0684815511018162 minutes
*** 37771 / 38220
Elapsed time: 1:29:53.720161
ETA: 1.0660736347912008 minutes
*** 37772 / 38220
Elapsed time: 1:29:53.915025
ETA: 1.0636658459746438 minutes
*** 37773 / 38220
Elapsed time: 1:29:54.094474
ETA: 1.0614549690263175 minutes
*** 37774 / 38220
Elapsed time: 1:29:54.255149
ETA: 1.059046988749166 minutes
*** 37775 / 38220
Elapsed time: 1:29:54.452905
ETA: 1.056639135959343 minutes
*** 37776 / 38220
Elapsed time: 1:29:54.621522
ETA: 1.0542314106466923 minutes
*** 37777 / 38220
Elapsed time: 1:29:54.793375
ETA: 1.0518238128011035 minu

Elapsed time: 1:30:13.081813
ETA: 0.8313912140336015 minutes
*** 37871 / 38220
Elapsed time: 1:30:13.301774
ETA: 0.8289871144909132 minutes
*** 37872 / 38220
Elapsed time: 1:30:13.569123
ETA: 0.8265831419040902 minutes
*** 37873 / 38220
Elapsed time: 1:30:13.872034
ETA: 0.8241792962630522 minutes
*** 37874 / 38220
Elapsed time: 1:30:14.173592
ETA: 0.8219273927392805 minutes
*** 37875 / 38220
Elapsed time: 1:30:14.509002
ETA: 0.8195233569190653 minutes
*** 37876 / 38220
Elapsed time: 1:30:14.780304
ETA: 0.8171194480379502 minutes
*** 37877 / 38220
Elapsed time: 1:30:15.175171
ETA: 0.8148661492158984 minutes
*** 37878 / 38220
Elapsed time: 1:30:15.543736
ETA: 0.8124620502125254 minutes
*** 37879 / 38220
Elapsed time: 1:30:15.860486
ETA: 0.8100580781414919 minutes
*** 37880 / 38220
Elapsed time: 1:30:16.100629
ETA: 0.8078033842823515 minutes
*** 37881 / 38220
Elapsed time: 1:30:16.322162
ETA: 0.8053992221459642 minutes
*** 37882 / 38220
Elapsed time: 1:30:16.538904
ETA: 0.8029951869352165

Elapsed time: 1:30:32.619158
ETA: 0.5840860215053757 minutes
*** 37975 / 38220
Elapsed time: 1:30:32.806393
ETA: 0.5816866793062218 minutes
*** 37976 / 38220
Elapsed time: 1:30:32.991917
ETA: 0.5792874634647281 minutes
*** 37977 / 38220
Elapsed time: 1:30:33.181529
ETA: 0.576994575807051 minutes
*** 37978 / 38220
Elapsed time: 1:30:33.359455
ETA: 0.5745951710155623 minutes
*** 37979 / 38220
Elapsed time: 1:30:33.530431
ETA: 0.5721958925750338 minutes
*** 37980 / 38220
Elapsed time: 1:30:33.703849
ETA: 0.5697967404755067 minutes
*** 37981 / 38220
Elapsed time: 1:30:33.879202
ETA: 0.5673977147069612 minutes
*** 37982 / 38220
Elapsed time: 1:30:34.068790
ETA: 0.5651028091514642 minutes
*** 37983 / 38220
Elapsed time: 1:30:34.250093
ETA: 0.5627035944959213 minutes
*** 37984 / 38220
Elapsed time: 1:30:34.417678
ETA: 0.5603045061647208 minutes
*** 37985 / 38220
Elapsed time: 1:30:34.617789
ETA: 0.5579055441478431 minutes
*** 37986 / 38220
Elapsed time: 1:30:34.797613
ETA: 0.5555067084353443 

Elapsed time: 1:30:50.919013
ETA: 0.33634024002731167 minutes
*** 38079 / 38220
Elapsed time: 1:30:51.107898
ETA: 0.3340073529411711 minutes
*** 38080 / 38220
Elapsed time: 1:30:51.314187
ETA: 0.331612877813086 minutes
*** 38081 / 38220
Elapsed time: 1:30:51.512188
ETA: 0.32921852843863536 minutes
*** 38082 / 38220
Elapsed time: 1:30:51.710784
ETA: 0.32682430480792085 minutes
*** 38083 / 38220
Elapsed time: 1:30:51.917554
ETA: 0.3244302069110442 minutes
*** 38084 / 38220
Elapsed time: 1:30:52.118406
ETA: 0.3220953131153995 minutes
*** 38085 / 38220
Elapsed time: 1:30:52.314489
ETA: 0.319701027499165 minutes
*** 38086 / 38220
Elapsed time: 1:30:52.505611
ETA: 0.31730686761011384 minutes
*** 38087 / 38220
Elapsed time: 1:30:52.713129
ETA: 0.31491283343834764 minutes
*** 38088 / 38220
Elapsed time: 1:30:52.901620
ETA: 0.31251892497396816 minutes
*** 38089 / 38220
Elapsed time: 1:30:53.097724
ETA: 0.31018202502844666 minutes
*** 38090 / 38220
Elapsed time: 1:30:53.276251
ETA: 0.30778792890

Elapsed time: 1:31:12.940093
ETA: 0.09076528207009081 minutes
*** 38182 / 38220
Elapsed time: 1:31:13.137401
ETA: 0.088390557752579 minutes
*** 38183 / 38220
Elapsed time: 1:31:13.345896
ETA: 0.08599937146448913 minutes
*** 38184 / 38220
Elapsed time: 1:31:13.540826
ETA: 0.0836083104185794 minutes
*** 38185 / 38220
Elapsed time: 1:31:13.722518
ETA: 0.08121737460499692 minutes
*** 38186 / 38220
Elapsed time: 1:31:13.901468
ETA: 0.07882656401393433 minutes
*** 38187 / 38220
Elapsed time: 1:31:14.065055
ETA: 0.07644984462832932 minutes
*** 38188 / 38220
Elapsed time: 1:31:14.241045
ETA: 0.07405884766118713 minutes
*** 38189 / 38220
Elapsed time: 1:31:14.420908
ETA: 0.07166797590992549 minutes
*** 38190 / 38220
Elapsed time: 1:31:14.588346
ETA: 0.06927722936469156 minutes
*** 38191 / 38220
Elapsed time: 1:31:14.755580
ETA: 0.06688660801564765 minutes
*** 38192 / 38220
Elapsed time: 1:31:14.947706
ETA: 0.06449611185295605 minutes
*** 38193 / 38220
Elapsed time: 1:31:15.104949
ETA: 0.0621170

In [5]:
ct = 1
results = {}
fast_ma, slow_ma, fast_period, slow_period = best_settings
for p in position_sizes:
    cash = 1000
    print(f'*** {ct} / {len(position_sizes)}')
    buys, sells = ma_cross_signal(fast_ma(train, timeperiod=fast_period),
                                  slow_ma(train, timeperiod=slow_period))
    buys = buys * train
    sells = sells * train
    orders = np.nan_to_num(buys) - np.nan_to_num(sells)
    orders = orders[orders != 0]
    if orders[0] < 0:
        orders = np.delete(orders, 0)
    if orders[-1] > 0:
        orders = np.delete(orders, -1)                        
    buys = orders[0::2]
    sells = - orders[1::2]
    profits = (sells / buys - 1) * (1 - fee)
    for profit in profits:
        cash += profit * p * cash
    results[cash] = p
    ct += 1
    elapsed = datetime.datetime.now() - start
    print(f'Elapsed time: {elapsed}')
    print(f'ETA: {(elapsed.seconds * n_runs / ct - elapsed.seconds) / 60} minutes')
max_cash = max(list(results.keys()))
print(f'Max cash: {max_cash}')
best_p = results[max_cash]
print(f'Best p: {best_p}')

*** 1 / 100
Elapsed time: 1:31:19.875235
ETA: 1744970.1833333333 minutes
*** 2 / 100
Elapsed time: 1:31:20.021171
ETA: 1163495.3333333333 minutes
*** 3 / 100
Elapsed time: 1:31:20.199997
ETA: 872598.6666666666 minutes
*** 4 / 100
Elapsed time: 1:31:20.384941
ETA: 698060.6666666666 minutes
*** 5 / 100
Elapsed time: 1:31:20.575816
ETA: 581702.0 minutes
*** 6 / 100
Elapsed time: 1:31:20.764749
ETA: 498588.6666666667 minutes
*** 7 / 100
Elapsed time: 1:31:20.948095
ETA: 436253.6666666667 minutes
*** 8 / 100
Elapsed time: 1:31:21.105859
ETA: 387841.65 minutes
*** 9 / 100
Elapsed time: 1:31:21.274489
ETA: 349048.35 minutes
*** 10 / 100
Elapsed time: 1:31:21.417290
ETA: 317308.37727272726 minutes
*** 11 / 100
Elapsed time: 1:31:21.542895
ETA: 290858.4 minutes
*** 12 / 100
Elapsed time: 1:31:21.684678
ETA: 268477.65 minutes
*** 13 / 100
Elapsed time: 1:31:21.852660
ETA: 249294.15 minutes
*** 14 / 100
Elapsed time: 1:31:22.012049
ETA: 232710.9 minutes
*** 15 / 100
Elapsed time: 1:31:22.159976
E

In [7]:
# Testing
cash = 1000
p = best_p
buys, sells = ma_cross_signal(fast_ma(close, timeperiod=fast_period)[-n_test:],
                              slow_ma(close, timeperiod=slow_period)[-n_test:])
buys = buys * test
sells = sells * test
orders = np.nan_to_num(buys) - np.nan_to_num(sells)
orders = orders[orders != 0]
if orders[0] < 0:
    orders = np.delete(orders, 0)
if orders[-1] > 0:
    orders = np.delete(orders, -1)                        
buys = orders[0::2]
sells = - orders[1::2]
profits = (sells / buys - 1) * (1 - fee)
for profit in profits:
    cash += profit * p * cash
print(f'Test results - Final cash: {cash}')
print(f'Number of test days: {n_test / 24}')

Test results - Final cash: 3505.1774281269213
Number of test days: 362.625
